In [1]:
import pandas as pd
import time as time

import numpy as np

In [2]:
import matplotlib.pyplot as plt
import seaborn as sns

In [3]:
import tensorflow as tf

In [4]:
pd.set_option('display.max_colwidth', None)
pd.set_option("display.max_rows", None, "display.max_columns", None)

## Load Datasets

In [5]:
s = time.time()
articles_df = pd.read_excel('data/articles_countries.xlsx', index_col=0, sheet_name='articles_countries')
e = time.time()
print("Multicore Loading Time = {}".format(e-s))

print(len(articles_df))
#clin_ner.info(verbose=True)

Multicore Loading Time = 12.908427476882935
32472


In [6]:
s = time.time()
size_df = pd.read_excel('data/final_sizes.xlsx', index_col=0, sheet_name='final_sizes')
e = time.time()
print("Multicore Loading Time = {}".format(e-s))

print(len(size_df))
#coarse_ner.info(verbose=True)

Multicore Loading Time = 5.36381459236145
32474


In [7]:
s = time.time()
ner_df = pd.read_excel('data/final_ner.xlsx', index_col=0, sheet_name='final_ner')
e = time.time()
print("Multicore Loading Time = {}".format(e-s))

print(len(ner_df))
#coarse_ner.info(verbose=True)

Multicore Loading Time = 28.081473112106323
32472


In [8]:
s = time.time()
affil_df = pd.read_csv('data/comm_affil.csv', index_col=0)
e = time.time()
print("Multicore Loading Time = {}".format(e-s))

print(len(ner_df))
#coarse_ner.info(verbose=True)

Multicore Loading Time = 0.22621870040893555
32472


## Clean base_data 

In [9]:
base_data = articles_df.copy()

In [10]:
base_data.isna().sum()

pmid                          0
doi                        4853
title                         0
abstract                      0
article_date               8351
pubmed_date                   0
article_type                  0
lang                          0
journal                       0
journal_short                 0
journal_country              45
authors                     785
author_affils             10248
keywords                  15194
mesh_terms                 8612
references_pmids          17098
feature                       0
include                       0
include_raw                   0
include_fuzzy                 0
affil_countries             102
affil_countries_unique      102
affil_first_country       10416
affil_last_country        10422
dtype: int64

In [11]:
## using first affiliation as country
## fill first with data from last author, then with pubmed country metadata
base_data['affil_first_country'] = base_data['affil_first_country'].fillna(base_data['affil_last_country'])
base_data['affil_first_country'] = base_data['affil_first_country'].fillna(base_data['journal_country'])

base_data['affil_first_country'] = base_data['affil_first_country'].astype('string')

In [12]:
##clean countries
base_data["affil_first_country"].replace({"England": "United Kingdom", 
                                             "Wales": "United Kingdom", 
                                             "Scotland": "United Kingdom", 
                                             "China (Republic : 1949- )" : "Taiwan"}, inplace=True)

base_data['affil_first_country'].value_counts()

United States             12118
China                      4773
United Kingdom             2696
Germany                    1217
South Korea                1182
Netherlands                1092
Japan                       810
India                       809
Canada                      718
Italy                       585
Spain                       518
Taiwan                      440
France                      413
Switzerland                 398
Australia                   396
Turkey                      363
Iran                        346
Brazil                      283
Ireland                     225
Israel                      190
Singapore                   190
Sweden                      169
Pakistan                    164
Greece                      154
Poland                      128
Saudi Arabia                122
Austria                     120
Finland                     120
Denmark                     120
Belgium                     111
Portugal                    109
Mexico  

In [13]:
base_data['countries_lc'] = base_data['affil_countries_unique'].str.lower()

In [14]:
## lmic_flag_all

lmic_list = ['afghanistan', 'albania', 'algeria', 'angola', 'antigua', 'barbuda', 'argentina', 'armenia', 'china',
             'azerbaijan', 'bangladesh', 'belarus', 'belize', 'benin', 'bhutan', 'bolivia', 'bosnia', 'herzegovina', 
             'botswana', 'brazil', 'burkina', 'faso', 'burundi', 'verde', 'cambodia', 'cameroon', 'africa', 'chad', 
             'colombia', 'comoros', 'congo', 'costa rica', 'ivoire', 'cuba', 'djibouti', 'dominica', 'dominica', 
             'ecuador', 'egypt', 'salvador', 'guinea', 'eritrea', 'eswatini', 'ethiopia', 'fiji', 'gabon', 'gambia', 
             'georgia', 'ghana', 'grenada', 'guatemala', 'guinea', 'guyana', 'haiti', 'honduras', 'india', 
             'indonesia', 'iran', 'iraq', 'jamaica', 'jordan', 'kazakhstan', 'kenya', 'kiribati', 'dpr', 'north korea', 
             'kosovo', 'kyrgyzstan', 'lao', 'lebanon', 'lesotho', 'liberia', 'libya', 'macedonia', 'madagascar', 'malawi', 
             'malaysia', 'maldives', 'mali', 'marshall', 'mauritania', 'mauritius', 'mexico', 'micronesia', 'moldova', 
             'mongolia', 'montenegro', 'montserrat', 'morocco', 'mozambique', 'myanmar', 'namibia', 'nauru', 'nepal', 
             'nicaragua', 'niger', 'nigeria', 'niue', 'pakistan', 'palau', 'panama', 'papua', 'paraguay', 'peru', 
             'philippines', 'rwanda', 'helena', 'samoa', 'príncipe', 'senegal', 'serbia', 'sierra leone', 'solomon', 
             'somalia', 'south africa', 'sudan', 'sri lanka', 'saint lucia', 'saint vincent', 'grenadines', 'sudan', 
             'suriname', 'syria', 'tajikistan', 'tanzania', 'thailand', 'timor', 'togo', 'tokelau', 'tonga', 'tunisia', 
             'turkey', 'turkmenistan', 'tuvalu', 'uganda', 'ukraine', 'uzbekistan', 'vanuatu', 'venezuela', 'vietnam', 
             'wallis', 'west bank', 'gaza', 'palestine', 'yemen', 'zambia', 'zimbabwe', 'low-income', 'middle-income', 
             'lmic', 'scarce']

lmic_lower_list = ['afghanistan', 'algeria', 'angola', 'antigua', 'barbuda',
             'azerbaijan', 'bangladesh', 'belize', 'benin', 'bhutan', 'bolivia', 'bosnia', 'herzegovina', 
             'burkina', 'faso', 'burundi', 'verde', 'cambodia', 'cameroon', 'africa', 'chad', 
             'comoros', 'congo', 'ivoire', 'djibouti',
             'ecuador', 'egypt', 'salvador', 'eritrea', 'eswatini', 'ethiopia', 'fiji', 'gabon', 'gambia', 
             'ghana', 'grenada', 'guatemala', 'guinea', 'guyana', 'haiti', 'honduras', 'india', 
             'indonesia', 'iran', 'jordan', 'kazakhstan', 'kenya', 'kiribati', 'dpr', 'north korea', 
             'kyrgyzstan', 'lao', 'lesotho', 'liberia', 'macedonia', 'madagascar', 'malawi', 
             'mali', 'mauritania', 'mexico', 'micronesia', 'moldova', 
             'mongolia', 'montenegro', 'montserrat', 'morocco', 'mozambique', 'myanmar', 'nauru', 'nepal', 
             'nicaragua', 'niger', 'nigeria', 'niue', 'pakistan', 'palau', 'panama', 'papua', 'paraguay', 'peru', 
             'philippines', 'rwanda', 'helena', 'samoa', 'príncipe', 'senegal', 'sierra leone', 'solomon', 
             'somalia', 'south africa', 'sudan', 'sri lanka', 'saint lucia', 'saint vincent', 'grenadines', 'sudan', 
             'suriname', 'syria', 'tajikistan', 'tanzania', 'thailand', 'timor', 'togo', 'tokelau', 'tonga', 'tunisia', 
             'uganda', 'ukraine', 'uzbekistan', 'vanuatu', 'venezuela', 'vietnam', 
             'wallis', 'west bank', 'gaza', 'palestine', 'yemen', 'zambia', 'zimbabwe', 'low-income', 'middle-income', 
             'lmic', 'scarce']

In [15]:
base_data['lmic_author_flag'] = np.where(base_data['countries_lc'].str.contains('iran'), "1", "0")
base_data['lmic_author_lower_flag'] = np.where(base_data['countries_lc'].str.contains('iran'), "1", "0")
base_data['lmic_china_flag'] = np.where(base_data['countries_lc'].str.contains('china'), "1", "0")

for x in lmic_list:
    base_data['lmic_author_flag'] = np.where(base_data['countries_lc'].str.contains(x), "1", base_data['lmic_author_flag'])
    
for y in lmic_lower_list:
    base_data['lmic_author_lower_flag'] = np.where(base_data['countries_lc'].str.contains(x), "1", base_data['lmic_author_lower_flag'])

In [16]:
## new column for year, and year+month
base_data['year'] = base_data['pubmed_date'].dt.year
base_data['date'] = base_data['pubmed_date']

In [17]:
## drop not needed for analysis

base_data = base_data.drop(['doi', 'article_date', 'lang', 'journal', 'authors', 
                            'keywords', 'pubmed_date', 'mesh_terms', 'references_pmids', 'feature', 'include_fuzzy',
                           'journal_country', 'author_affils', 'affil_countries', 'affil_last_country',
                           'countries_lc', 'affil_countries_unique', 'include_raw'], axis=1)

base_data = base_data.rename(columns={"include": "mature_flag"})

In [18]:
##mask countries below first 12
occurrence = base_data['affil_first_country'].value_counts()

condition = occurrence < 440
mask = occurrence[condition].index
mask_dict = dict.fromkeys(mask, 'Other')

base_data['affil_country_masked'] = base_data['affil_first_country'].replace(mask_dict)

#total_country_output = base_data['affil_country_masked'].value_counts().rename_axis('country').reset_index(name='counts')
#total_country_output

In [19]:
base_data.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 32472 entries, 0 to 161524
Data columns (total 13 columns):
 #   Column                  Non-Null Count  Dtype         
---  ------                  --------------  -----         
 0   pmid                    32472 non-null  int64         
 1   title                   32472 non-null  object        
 2   abstract                32472 non-null  object        
 3   article_type            32472 non-null  object        
 4   journal_short           32472 non-null  object        
 5   mature_flag             32472 non-null  int64         
 6   affil_first_country     32470 non-null  object        
 7   lmic_author_flag        32472 non-null  object        
 8   lmic_author_lower_flag  32472 non-null  object        
 9   lmic_china_flag         32472 non-null  object        
 10  year                    32472 non-null  int64         
 11  date                    32472 non-null  datetime64[ns]
 12  affil_country_masked    32470 non-null  objec

In [20]:
base_data['mature_flag'].value_counts()

0    31305
1     1167
Name: mature_flag, dtype: int64

In [21]:
base_data = base_data.sort_index()
base_data.tail(15)

pmid  \
161465  9470396   
161479  9431637   
161482  9458164   
161485  9457438   
161486  9457435   
161490  9456211   
161496  9453525   
161502  9450258   
161506  9445150   
161507  9440819   
161510  9438272   
161511  9438271   
161513  9436967   
161517  9430460   
161524  9423655   

                                                                                                                                                                                            title  \
161465                                                                                                                Decision support for psychiatric diagnosis based on a simple questionnaire.   
161479                                                                                    Classification of low back pain from dynamic motion characteristics using an artificial neural network.   
161482                                                                       Improving morphology-based malignancy grading schemes in astrocytic tumors by means of computer-assisted techniques.   
161485                                                                                                                             Ventilation mode recognition using artificial neural networks.   
161486                                                                                                                             Automated detection of hereditary syndromes using data mining.   
161490                                                                                                      Neural network assessment of perioperative cardiac risk in vascular surgery patients.   
161496                                                                                                 TACHY: an expert system for the management of supraventricular tachycardia in the elderly.   
161502                                                                                                                                             Detection of ECG waveforms by neural networks.   
161506                                                                                                                                Neural network analysis of breast cancer from MRI findings.   
161507                                                 Automated classification of patients with chronic lymphocytic leukemia and immunocytoma from flow cytometric three-color immunophenotypes.   
161510  On the use of neural network techniques to analyze sleep EEG data. Third communication: robustification of the classificator by applying an algorithm obtained from 9 different networks.   
161511                                                                       Analysis of quantitative EEG with artificial neural networks and discriminant analysis--a methodological comparison.   
161513                                                                                               Neural networks as a prognostic tool for patients with non-small cell carcinoma of the lung.   
161517                                                                                            Automated interpretation of myocardial SPECT perfusion images using artificial neural networks.   
161524                                                                         Acute pulmonary embolism: cost-effectiveness analysis of the effect of artificial neural networks on patient care.   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                         

## Clean ner_data 

In [22]:
ner_data = ner_df.drop(['countries', 'text', 'lmic_flag'], axis=1)

In [23]:
ner_data.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 32472 entries, 0 to 77604
Data columns (total 83 columns):
 #   Column               Non-Null Count  Dtype
---  ------               --------------  -----
 0   algo_neural_net      32472 non-null  int64
 1   algo_support_vector  32472 non-null  int64
 2   algo_regression      32472 non-null  int64
 3   algo_decision_tree   32472 non-null  int64
 4   algo_discriminant    32472 non-null  int64
 5   algo_naive_bayes     32472 non-null  int64
 6   algo_transfer        32472 non-null  int64
 7   algo_federated       32472 non-null  int64
 8   algo_k_nearest       32472 non-null  int64
 9   algo_unsupervised    32472 non-null  int64
 10  feat_imaging         32472 non-null  int64
 11  feat_xr              32472 non-null  int64
 12  feat_ct              32472 non-null  int64
 13  feat_mri             32472 non-null  int64
 14  feat_eeg             32472 non-null  int64
 15  feat_ecg             32472 non-null  int64
 16  feat_us              3

In [24]:
ner_data = ner_data.sort_index()
ner_data.tail(15)

algo_neural_net  algo_support_vector  algo_regression  \
index                                                           
161465                1                    0                0   
161479                1                    0                0   
161482                0                    0                0   
161485                1                    0                0   
161486                0                    0                0   
161490                1                    0                1   
161496                0                    0                0   
161502                1                    0                0   
161506                1                    0                0   
161507                0                    0                0   
161510                1                    0                0   
161511                1                    0                0   
161513                1                    0                0   
161517                1                    0                0   
161524                1                    0                0   

        algo_decision_tree  algo_discriminant  algo_naive_bayes  \
index                                                             
161465                   0                  0                 0   
161479                   0                  0                 0   
161482                   1                  0                 0   
161485                   0                  0                 0   
161486                   0                  0                 0   
161490                   0                  0                 0   
161496                   0                  0                 0   
161502                   0                  0                 0   
161506                   0                  0                 0   
161507                   0                  0                 0   
161510                   0                  0                 0   
161511                   0                  1                 0   
161513                   0                  0                 0   
161517                   0                  0                 0   
161524                   0                  0                 0   

        algo_transfer  algo_federated  algo_k_nearest  algo_unsupervised  \
index                                                                      
161465              0               0               0                  0   
161479              0               0               0                  0   
161482              0               0               0                  0   
161485              0               0               0                  0   
161486              0               0               0                  0   
161490              0               0               0                  0   
161496              0               0               0                  0   
161502              0               0               0                  0   
161506              0               0               0                  0   
161507              0               0               0                  0   
161510              0               0               0                  0   
161511              0               0               0                  0   
161513              0               0               0                  0   
161517              0               0               0                  0   
161524              0               0               0                  0   

        feat_imaging  feat_xr  feat_ct  feat_mri  feat_eeg  feat_ecg  feat_us  \
index                                                                           
161465             0        0        0         0         0         0        0   
161479             0        0        0         0         0         0        0   
161482             0        0        0         0         0         0        0   
161485             0        0        0         0         0      

In [25]:
#create null file for manual review

null = ner_data.loc[(ner_data==0).all(axis=1)]

In [26]:
#null['text'] = ner_df['text'].copy() 

In [27]:
#null.to_csv('ner_null.csv')

len(null)

919

In [28]:
## INTENSIVE CARE MEDICINE / icu
## EMERGENCY MEDICINE / ed
## INFECTIONS [C01] / id
    #### SEPSIS / sepsis
    #### COVID-19 / cov19
    #### MALARIA / malaria
    #### HIV / hiv
    #### TB / tb
## DERMATOLOGY [C17] / derm
    ####SKIN CANCERS / dermca
## NEOPLASMS [C04] / onc
    #### RADIOTHERAPY / rx
    #### LUNG / lungca
    #### NEURO / neuroca
    #### GI / gica
    #### HPB / hepca
    #### GYNAE / gynonc
    #### PROSTATE / prosca
    #### RENAL / renalca
    #### HAEM / haemonc
## BREAST / breast (<- almost entirely onc)
## PSYCHIATRY / psych
    #### SUICIDE / suicide
## MUSCULOSKELETAL [C05] / msk
    #### FRACTURE / frac
## CONNECTIVE TISSUE [C17] / rheum
## GASTROINTESTINAL [C06] / gi
## HEPATOLOGY & BILIARY [C06] / hep
## RESPIRATORY [C08] / resp
    #### PNEUMONIA / pneum
## NERVOUS SYSTEM [C10] / neuro
    #### STROKE / cva
    #### SEIZURE / epilep
    #### DEMENTIA / alzh
## CARDIOVASCULAR [C14] / cvs
    #### ISCHAEMIC HEART DISEASE / ihd
    #### CARDIAC FAILURE / hf
## ENDOCRINE [C19] / endo
    #### DIABETES / dm
## OPHTHALMOLOGY [C11] / eye
    #### RETINOPATHIES / retina
## HAEMATOLOGIC [C15] / haem
## GYNAE/OBSTETRIC [C13] / obs
## NEPHROLOGY [C12] / renal
    #### ACUTE & CHRONIC KIDNEY / ackd
## PAEDIATRICS / paeds
## STOMATOGNATHIC [C07] / dental
## AUDIOLOGY [C09] / ent
## PUBLIC HEALTH / pubh
## BCI
## PROSTHESIS CONTROL
## WHEELCHAIR CONTROL
## HOME SENSORS

## Clean size_data

In [29]:
size_df['ptdata_size'] = size_df[['patient_size', 'n_size']].max(axis=1)

In [30]:
size_data = size_df[['ptdata_size', 'feature_size']].copy().astype(int)

In [31]:
size_data = size_data.replace(0, np.nan)

In [32]:
size_data.info()

<class 'pandas.core.frame.DataFrame'>
Index: 32474 entries, 86876 to 161524
Data columns (total 2 columns):
 #   Column        Non-Null Count  Dtype  
---  ------        --------------  -----  
 0   ptdata_size   7822 non-null   float64
 1   feature_size  5558 non-null   float64
dtypes: float64(2)
memory usage: 761.1+ KB


In [33]:
size_data.sample(5)

ptdata_size  feature_size
index                            
152330         12.0         384.0
70139           NaN         333.0
25553          86.0           NaN
129212          NaN           NaN
40971           NaN           NaN

## Clean affil data

In [34]:
affil_data = affil_df['comm_flag'].copy()

In [35]:
affil_data = affil_data.sort_index()
affil_data.sample(50)

99286     0
12718     0
111161    0
151895    0
15807     1
54714     0
30543     1
91109     0
26826     0
9573      0
150614    0
79763     0
15392     0
97933     0
58710     0
70210     0
114935    0
138934    0
8553      0
97586     0
41530     0
90746     0
43639     0
59003     0
23133     0
153513    0
84426     0
110687    0
101987    0
77100     0
54778     0
34014     0
16547     1
81437     1
79577     0
146058    0
36577     0
68826     0
40233     0
2174      1
155583    0
96871     0
44227     0
94752     0
21167     0
94893     0
17974     0
18902     0
16992     0
55358     0
Name: comm_flag, dtype: int64

## Combine datasets

In [36]:
raw_joined = pd.concat([base_data, ner_data, size_data, affil_data], axis=1)

print(len(raw_joined))

32474


In [37]:
raw_joined.info()

<class 'pandas.core.frame.DataFrame'>
Index: 32474 entries, 0 to al Center
Data columns (total 99 columns):
 #   Column                  Non-Null Count  Dtype         
---  ------                  --------------  -----         
 0   pmid                    32472 non-null  float64       
 1   title                   32472 non-null  object        
 2   abstract                32472 non-null  object        
 3   article_type            32472 non-null  object        
 4   journal_short           32472 non-null  object        
 5   mature_flag             32472 non-null  float64       
 6   affil_first_country     32470 non-null  object        
 7   lmic_author_flag        32472 non-null  object        
 8   lmic_author_lower_flag  32472 non-null  object        
 9   lmic_china_flag         32472 non-null  object        
 10  year                    32472 non-null  float64       
 11  date                    32472 non-null  datetime64[ns]
 12  affil_country_masked    32470 non-null  object 

In [38]:
raw_joined.sample(5)

pmid  \
19128  33360973.0   
99647  25929619.0   
8078   33925256.0   
32091  32717848.0   
41322  32166491.0   

                                                                                                                                                                 title  \
19128                                                                           GAMER MRI: Gated-attention mechanism ranking of multi-contrast MRI in brain pathology.   
99647        Using within-subject pattern classification to understand lifespan age differences in oscillatory mechanisms of working memory selection and maintenance.   
8078                                A Machine Learning Decision Support System (DSS) for Neuroendocrine Tumor Patients Treated with Somatostatin Analog (SSA) Therapy.   
32091                        Classification of Neurological Patients to Identify Fallers Based on Spatial-Temporal Gait Characteristics Measured by a Wearable Device.   
41322  Artificial intelligence and radiomics enhance the positive predictive value of digital chest tomosynthesis for lung cancer detection within SOS clinical trial.   

                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                               abstract  \
19128                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                                              During the last decade, a multitude of novel quantitative and semiquantitative MRI techniques have provided new information about the pathophysiology of neurological diseases. Yet, selection of the most relevant contrasts for a given pathology remains challenging. In this work, we developed and validated a method, Gated-Attention MEchanism Ranking of multi-contrast MRI in brain pathology (GAMER MRI), to rank the relative importance of MR measures 

In [39]:
raw_joined = raw_joined.dropna(how='all')

In [40]:
all_ner = ['algo_neural_net', 'algo_support_vector', 'algo_regression', 'algo_decision_tree', 
            'algo_discriminant', 'algo_naive_bayes', 'algo_transfer', 'algo_federated', 'algo_k_nearest',
            'algo_unsupervised',
           #
            'feat_imaging', 'feat_xr', 'feat_ct', 'feat_mri', 'feat_eeg', 'feat_ecg',
            'feat_us', 'feat_echo', 'feat_histo', 'feat_oct', 'feat_mamm', 'feat_endoscop', 'feat_derm',
            'feat_gene', 'feat_bio', 'feat_nlp', 'feat_ehr', 'feat_sensor', 'feat_phone', 
           # 
           'subspec_icu', 'subspec_ed', 'spec_id', 'subspec_sepsis', 'subspec_hiv', 'subspec_cov19', 'subspec_tb',
            'subspec_malaria', 'spec_derm', 'subspec_dermca', 'spec_onc', 'subspec_rx', 'subspec_gynonc', 
            'subspec_lungca', 'subspec_brainca', 'subspec_gica', 'subspec_hepca', 'subspec_prosca',
            'subspec_renalca', 'subspec_haemonc', 'subspec_breast', 'spec_psych','subspec_suicide', 'spec_msk', 
            'subspec_frac', 'spec_rheum', 'spec_gi', 'spec_hep', 'spec_resp', 'subspec_pneum',
            'spec_neuro', 'subspec_epilep', 'subspec_cva', 'subspec_alzh', 'spec_cvs', 'subspec_ihd', 'subspec_hf', 
            'spec_endo', 'subspec_dm', 'spec_eye', 'subspec_retina', 'spec_haem', 'spec_obs', 'spec_renal', 
            'subspec_ackd', 'spec_paeds', 'spec_dent',  'spec_audio', 'spec_pubh', 'subspec_bci',
            'subspec_prosth', 'subspec_arrhyt', 'subspec_assist','subspec_activity']

for x in all_ner:
    raw_joined[x] = raw_joined[x].astype(int)

In [98]:
raw_joined.to_csv('for_export/clean/raw_joined.csv')

## Add comparative flags for all

In [53]:
ner_cats = raw_joined[['algo_neural_net', 'algo_support_vector', 'algo_regression', 'algo_decision_tree', 
            'algo_discriminant', 'algo_naive_bayes', 'algo_transfer', 'algo_federated', 'algo_k_nearest',
            'algo_unsupervised',
           #
            'feat_imaging', 'feat_xr', 'feat_ct', 'feat_mri', 'feat_eeg', 'feat_ecg',
            'feat_us', 'feat_echo', 'feat_histo', 'feat_oct', 'feat_mamm', 'feat_endoscop', 'feat_derm',
            'feat_gene', 'feat_bio', 'feat_nlp', 'feat_ehr', 'feat_sensor', 'feat_phone', 
           # 
           'subspec_icu', 'subspec_ed', 'spec_id', 'subspec_sepsis', 'subspec_hiv', 'subspec_cov19', 'subspec_tb',
            'subspec_malaria', 'spec_derm', 'subspec_dermca', 'spec_onc', 'subspec_rx', 'subspec_gynonc', 
            'subspec_lungca', 'subspec_brainca', 'subspec_gica', 'subspec_hepca', 'subspec_prosca',
            'subspec_renalca', 'subspec_haemonc', 'subspec_breast', 'spec_psych','subspec_suicide', 'spec_msk', 
            'subspec_frac', 'spec_rheum', 'spec_gi', 'spec_hep', 'spec_resp', 'subspec_pneum',
            'spec_neuro', 'subspec_epilep', 'subspec_cva', 'subspec_alzh', 'spec_cvs', 'subspec_ihd', 'subspec_hf', 
            'spec_endo', 'subspec_dm', 'spec_eye', 'subspec_retina', 'spec_haem', 'spec_obs', 'spec_renal', 
            'subspec_ackd', 'spec_paeds', 'spec_dent',  'spec_audio', 'spec_pubh', 'subspec_bci',
            'subspec_prosth', 'subspec_arrhyt', 'subspec_assist','subspec_activity', 
            #
            'mature_flag']].copy()


In [54]:
## subset of mature studies
ner_comparative = ner_cats.loc[ner_cats['mature_flag'] == 1].drop(['mature_flag'], axis=1).astype(int)

In [55]:
## rename columns
ner_comparative = ner_comparative.rename(columns=lambda x: 'mature_' + x)

In [56]:
ner_comparative.info()

<class 'pandas.core.frame.DataFrame'>
Index: 1167 entries, 58 to 161506
Data columns (total 83 columns):
 #   Column                      Non-Null Count  Dtype
---  ------                      --------------  -----
 0   mature_algo_neural_net      1167 non-null   int32
 1   mature_algo_support_vector  1167 non-null   int32
 2   mature_algo_regression      1167 non-null   int32
 3   mature_algo_decision_tree   1167 non-null   int32
 4   mature_algo_discriminant    1167 non-null   int32
 5   mature_algo_naive_bayes     1167 non-null   int32
 6   mature_algo_transfer        1167 non-null   int32
 7   mature_algo_federated       1167 non-null   int32
 8   mature_algo_k_nearest       1167 non-null   int32
 9   mature_algo_unsupervised    1167 non-null   int32
 10  mature_feat_imaging         1167 non-null   int32
 11  mature_feat_xr              1167 non-null   int32
 12  mature_feat_ct              1167 non-null   int32
 13  mature_feat_mri             1167 non-null   int32
 14  mature_fea

## Add oncology flags for all

In [57]:
## subset of oncology studies
ner_oncology = ner_cats.loc[ner_cats['spec_onc'] == 1].drop(['mature_flag', 'spec_onc'], axis=1).astype(int)

In [58]:
## rename columns
ner_oncology = ner_oncology.rename(columns=lambda x: 'onc_' + x)

In [59]:
ner_oncology.info()

<class 'pandas.core.frame.DataFrame'>
Index: 9237 entries, 0 to 161513
Data columns (total 82 columns):
 #   Column                   Non-Null Count  Dtype
---  ------                   --------------  -----
 0   onc_algo_neural_net      9237 non-null   int32
 1   onc_algo_support_vector  9237 non-null   int32
 2   onc_algo_regression      9237 non-null   int32
 3   onc_algo_decision_tree   9237 non-null   int32
 4   onc_algo_discriminant    9237 non-null   int32
 5   onc_algo_naive_bayes     9237 non-null   int32
 6   onc_algo_transfer        9237 non-null   int32
 7   onc_algo_federated       9237 non-null   int32
 8   onc_algo_k_nearest       9237 non-null   int32
 9   onc_algo_unsupervised    9237 non-null   int32
 10  onc_feat_imaging         9237 non-null   int32
 11  onc_feat_xr              9237 non-null   int32
 12  onc_feat_ct              9237 non-null   int32
 13  onc_feat_mri             9237 non-null   int32
 14  onc_feat_eeg             9237 non-null   int32
 15  onc_fea

## Join sub ner dfs 

In [60]:
temp = pd.concat([raw_joined, ner_comparative, ner_oncology], axis=1).astype(int, errors='ignore')

In [61]:
len(temp)

32472

In [62]:
joined = temp.fillna(0).astype(int, errors='ignore')

In [63]:
joined['total'] = 1

In [64]:
joined.info(verbose=True)

<class 'pandas.core.frame.DataFrame'>
Int64Index: 32472 entries, 0 to 161524
Data columns (total 265 columns):
 #    Column                      Dtype         
---   ------                      -----         
 0    pmid                        int32         
 1    title                       object        
 2    abstract                    object        
 3    article_type                object        
 4    journal_short               object        
 5    mature_flag                 int32         
 6    affil_first_country         object        
 7    lmic_author_flag            int32         
 8    lmic_author_lower_flag      int32         
 9    lmic_china_flag             int32         
 10   year                        int32         
 11   date                        datetime64[ns]
 12   affil_country_masked        object        
 13   algo_neural_net             int32         
 14   algo_support_vector         int32         
 15   algo_regression             int32         
 16   a

In [65]:
#temp = joined_by_date.drop(['pmid', 'abstract', 'title', 'article_type', 'journal_short', 'affil_countries_unique', 'affil_first_country',
#                          'countries_lc', 'date', 'affil_country_masked', 'feature_size', 'ptdata_size'], axis=1)

In [66]:
#temp = temp[temp['year'].notna()]

In [67]:
joined_by_year = joined.groupby(['year']).sum().astype(int).drop(['pmid'], axis=1)

In [68]:
joined_by_year

mature_flag  lmic_author_flag  lmic_author_lower_flag  lmic_china_flag  \
year                                                                           
1998            9                 0                       0                0   
1999           18                 1                       1                1   
2000           15                 0                       0                0   
2001           15                 1                       1                1   
2002           13                 0                       0                0   
2003            8                 0                       0                0   
2004           20                 3                       0                0   
2005           10                 3                       0                1   
2006           22                 2                       0                0   
2007           18                 9                       0                1   
2008           19                11                       0                0   
2009           17                 9                       0                0   
2010            7                10                       0                0   
2011           13                17                       3                2   
2012           10                 7                       4                1   
2013            9                29                       3                7   
2014           14               201                      18              103   
2015           15               257                      23              100   
2016           14               324                      27              148   
2017           51               513                      44              244   
2018           99               835                      45              438   
2019          191              1576                      83              975   
2020          322              2588                     126             1702   
2021          238              2270                     119             1421   

      algo_neural_net  algo_support_vector  algo_regression  \
year                                                          
1998              108                    0               13   
1999              107                    0               18   
2000              114                    1               19   
2001              126                    2               17   
2002              136                    3               17   
2003              125                    9               24   
2004              154                   22               26   
2005              161                   34               26   
2006              169                   32               23   
2007              190                   71               37   
2008              152                   78               19   
2009              183                  113               35   
2010              192                  125               33   
2011              151                  136               34   
2012              136                  189               40   
2013              179                  266               57   
2014              176                  238               52   
2015              170                  315               53   
2016              272                  303               62   
2017              554                  394               93   
2018             1133                  449              175   
2019             1944                  509              281   
2020             3501                  661              443   
2021             2607                  412              325   

      algo_decision_tree  algo_discriminant  algo_naive_bayes  algo_transfer  \
year                                                                           
1998                   4                  5                 1              0   
1999                   3                  9   

In [69]:
joined_by_year.to_csv('for_export/clean/joined_by_year.csv')

In [70]:
joined.to_csv('for_export/clean/joined_by_date.csv')

## Dot matrix counts

In [71]:
for_transpose = joined.drop(['pmid', 'abstract', 'title', 'article_type', 'journal_short', 'affil_first_country', 
                             'year', 'date', 'affil_country_masked', 
                             #'feature_size', 'ptdata_size'
                            ], axis=1)

In [72]:
#temp = pd.concat([spec_by_year, feat_by_year], axis=1).astype(int)
#for_transpose = pd.concat([temp, subspec_by_year], axis=1).astype(int)
#
#for_transpose['mature_flag'] = joined['mature_flag'].copy()
#for_transpose['lmic_flag'] = joined['lmic_author_flag'].copy()
#for_transpose['lmic_lower_flag'] = joined['lmic_author_lower_flag'].copy()
#for_transpose['lmic_china_flag'] = joined['lmic_china_flag'].copy()

for_transpose.head(50)

mature_flag  lmic_author_flag  lmic_author_lower_flag  lmic_china_flag  \
0              0                 0                       0                0   
2              0                 0                       0                0   
3              0                 0                       0                0   
9              0                 0                       0                0   
15             0                 0                       0                0   
20             0                 0                       0                0   
24             0                 0                       0                0   
37             0                 0                       0                0   
39             0                 0                       0                0   
43             0                 1                       0                1   
44             0                 1                       0                1   
47             0                 0                       0                0   
49             0                 1                       0                1   
53             0                 0                       0                0   
54             0                 1                       0                1   
56             0                 1                       0                1   
58             1                 0                       0                0   
59             0                 0                       0                0   
62             0                 0                       0                0   
63             0                 0                       0                0   
70             0                 1                       0                0   
72             0                 1                       0                0   
82             0                 0                       0                0   
83             0                 1                       1                0   
84             0                 0                       0                0   
86             0                 0                       0                0   
87             0                 0                       0                0   
88             0                 0                       0                0   
89             0                 0                       0                0   
91             0                 0                       0                0   
94             0                 1                       0                0   
101            1                 1                       0                0   
102            0                 0                       0                0   
104            0                 0                       0                0   
108            0                 1                       0                1   
110            0                 1                       0                0   
117            0                 0                       0                0   
118            0                 1                       0                1   
125            0                 0                       0                0   
126            0                 0                       0                0   
132            0                 0                       0                0   
143            0                 1                       0                1   
146            1                 0                       0                0   
150            0                 0                       0                0   
155            0                 1                       0                0   
156            0                 0                       0                0   
159            0                 1                       1                1   
163            0                 0                       0                0   
165            0                 0                       0                0   
172            0                 0                     

In [73]:
for_transpose = for_transpose.astype(int)

In [74]:
transposed = for_transpose.T

In [75]:
transposed.info()

<class 'pandas.core.frame.DataFrame'>
Index: 256 entries, mature_flag to total
Columns: 32472 entries, 0 to 161524
dtypes: int32(32472)
memory usage: 31.7+ MB


In [76]:
matrix = transposed.dot(for_transpose).astype(int)

In [77]:
matrix['total'] = (pd.Series(np.diag(matrix), index=[matrix.index, matrix.columns])).tolist()

In [78]:
matrix

mature_flag  lmic_author_flag  \
mature_flag                        1167               208   
lmic_author_flag                    208              8666   
lmic_author_lower_flag                8               497   
lmic_china_flag                     141              5145   
algo_neural_net                     687              3650   
algo_support_vector                  31              1394   
algo_regression                      31               477   
algo_decision_tree                   24               739   
algo_discriminant                     5               147   
algo_naive_bayes                      2                87   
algo_transfer                        24               298   
algo_federated                        0                 6   
algo_k_nearest                        3               199   
algo_unsupervised                     4               150   
feat_imaging                        505              3051   
feat_xr                             145               377   
feat_ct                             202              1005   
feat_mri                            124              1055   
feat_eeg                             12               483   
feat_ecg                             26               285   
feat_us                             104               376   
feat_echo                            26                59   
feat_histo                          150               576   
feat_oct                             23               121   
feat_mamm                            59               124   
feat_endoscop                        58               124   
feat_derm                            33                54   
feat_gene                             6               611   
feat_bio                             25               846   
feat_nlp                             34                46   
feat_ehr                             66               547   
feat_sensor                           6               162   
feat_phone                           15                68   
subspec_icu                          14               159   
subspec_ed                           35                45   
spec_id                              88              1038   
subspec_sepsis                        5                62   
subspec_hiv                           4                25   
subspec_cov19                        32               509   
subspec_tb                            8               105   
subspec_malaria                       1                29   
spec_derm                            64               189   
subspec_dermca                       52               115   
spec_onc                            478              3007   
subspec_rx                           15               177   
subspec_gynonc                       18               168   
subspec_lungca                       80               456   
subspec_brainca                      17               338   
subspec_gica                         61               359   
subspec_hepca                        14               256   
subspec_prosca                       33               127   
subspec_renalca                      11                97   
subspec_haemonc                      11               108   
subspec_breast                      134               555   
spec_psych                           26               638   
subspec_suicide                       7               175   
spec_msk                             74               198   
subspec_frac                         30                38   
spec_rheum                            4                33   
spec_gi                              79               471   
spec_hep                             25               398   
spec_resp                           175              1049   
subspec_pneum                        35               247   
spec_neuro                          107              1766   
subspec_epilep                       17               450   
su

In [79]:
matrix.to_csv('for_export/clean/matrix.csv')